<a href="https://colab.research.google.com/github/nirvana66649/felixRepo/blob/main/gpt2_summarization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import random
import numpy as np
import torch
import torch.nn.functional as F
from transformers import GPT2Tokenizer
from tqdm import tnrange


def add_special_tokens():
	""" Returns GPT2 tokenizer after adding separator and padding tokens """
	tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
	special_tokens = {'pad_token':'<|pad|>','sep_token':'<|sep|>'}
	num_add_toks = tokenizer.add_special_tokens(special_tokens)
	return tokenizer

def set_seed(args):
    random.seed(args.seed)
    np.random.seed(args.seed)
    torch.manual_seed(args.seed)
    if args.n_gpu > 0:
        torch.cuda.manual_seed_all(args.seed)


def top_k_top_p_filtering(logits, top_k=0, top_p=0.0, filter_value=-float('Inf')):
    """ Filter a distribution of logits using top-k and/or nucleus (top-p) filtering
        Args:
            logits: logits distribution shape (vocabulary size)
            top_k > 0: keep only top k tokens with highest probability (top-k filtering).
            top_p > 0.0: keep the top tokens with cumulative probability >= top_p (nucleus filtering).
                Nucleus filtering is described in Holtzman et al. (http://arxiv.org/abs/1904.09751)
        From: https://gist.github.com/thomwolf/1a5a29f6962089e871b94cbd09daf317
    """
    assert logits.dim() == 1  # batch size 1 for now - could be updated for more but the code would be less clear
    top_k = min(top_k, logits.size(-1))  # Safety check
    if top_k > 0:
        # Remove all tokens with a probability less than the last token of the top-k
        indices_to_remove = logits < torch.topk(logits, top_k)[0][..., -1, None]
        logits[indices_to_remove] = filter_value

    if top_p > 0.0:
        sorted_logits, sorted_indices = torch.sort(logits, descending=True)
        cumulative_probs = torch.cumsum(F.softmax(sorted_logits, dim=-1), dim=-1)

        # Remove tokens with cumulative probability above the threshold
        sorted_indices_to_remove = cumulative_probs > top_p
        # Shift the indices to the right to keep also the first token above the threshold
        sorted_indices_to_remove[..., 1:] = sorted_indices_to_remove[..., :-1].clone()
        sorted_indices_to_remove[..., 0] = 0

        indices_to_remove = sorted_indices[sorted_indices_to_remove]
        logits[indices_to_remove] = filter_value
    return logits


def sample_seq(model, context, length, device, temperature=1, top_k=0, top_p=0.0):
    """ Generates a sequence of tokens
        Args:
            model: gpt/gpt2 model
            context: tokenized text using gpt/gpt2 tokenizer
            length: length of generated sequence.
            device: torch.device object.
            temperature >0: used to control the randomness of predictions by scaling the logits before applying softmax.
            top_k > 0: keep only top k tokens with highest probability (top-k filtering).
            top_p > 0.0: keep the top tokens with cumulative probability >= top_p (nucleus filtering).
    """

    context = torch.tensor(context, dtype=torch.long, device=device)
    context = context.unsqueeze(0)
    generated = context
    with torch.no_grad():
        for _ in tnrange(length):
            inputs = {'input_ids': generated}
            outputs = model(**inputs)  # Note: we could also use 'past' with GPT-2/Transfo-XL/XLNet (cached hidden-states)
            next_token_logits = outputs[0][0, -1, :] / temperature
            filtered_logits = top_k_top_p_filtering(next_token_logits, top_k=top_k, top_p=top_p)
            next_token = torch.multinomial(F.softmax(filtered_logits, dim=-1), num_samples=1)
            generated = torch.cat((generated, next_token.unsqueeze(0)), dim=1)
    return generated


def beam_search(model, context, length, beam_size, device, temperature=1):
    """ Generate sequence using beam search https://machinelearningmastery.com/beam-search-decoder-natural-language-processing/
        Args:
            model: gpt/gpt2 model
            context: tokenized text using gpt/gpt2 tokenizer
            length: length of generated sequence.
            beam_size: >=1 and <= total_no_of_tokens
            device: torch.device object.
            temperature >0: used to control the randomness of predictions by scaling the logits before applying softmax.
    """
    context = torch.tensor(context, dtype=torch.long, device=device)
    context = context.unsqueeze(0)
    with torch.no_grad():
        inputs = {'input_ids': context}
        outputs = model(**inputs)
        next_token_logits = outputs[0][0, -1, :] / temperature
        next_token_probs = F.softmax(next_token_logits)
        scores, indices = torch.topk(next_token_probs, beam_size)
        indices = indices.tolist()
        sequences = [[c] for c in indices]
        for _ in tnrange(length-1):
            logits = torch.zeros(beam_size*len(next_token_logits))
            for j in range(len(sequences)):
                new_generated = torch.cat((context,torch.tensor([sequences[j]], dtype=torch.long, device=device)),dim=1)
                inputs = {'input_ids': new_generated}
                outputs = model(**inputs)
                next_token_logits = outputs[0][0, -1, :] / temperature
                next_token_probs = F.softmax(next_token_logits)
                start, stop = j*len(next_token_logits), (j+1)*len(next_token_logits)
                logits[start:stop] = scores[j]*next_token_probs
            scores, new_logits_indices = torch.topk(logits,beam_size)
            logits = (new_logits_indices%50259).tolist()
            for j in range(len(sequences)):
                sequences[j] = sequences[j]+[logits[j]]
    return scores, sequences


def generate_beam_sample(data, tokenizer, model, num=1, length=100, beam_size=3, device=torch.device('cuda')):
    """ Generate summaries for "num" number of articles using beam search.
        Args:
            data = GPT21024Dataset object
            tokenizer = gpt/gpt2 tokenizer
            num = number of articles for which summaries has to be generated
    """
    for i in range(num):
        sample = data[i]
        idx = sample['sum_idx']
        context = sample['article'][:idx].tolist()
        summary = sample['article'][idx+1:][:100].tolist()
        scores, sequences = beam_search(model, context, length, beam_size, device)
        print('new_article', end='\n\n')
        print(tokenizer.decode(context[:-1]), end='\n\n')
        print('actual_summary', end='\n\n')
        print(tokenizer.decode(summary), end='\n\n')
        for i in range(len(sequences)):
            text = tokenizer.convert_ids_to_tokens(sequences[i],skip_special_tokens=True)
            text = tokenizer.convert_tokens_to_string(text)
            print("generated_summary-{} and Score is {}.".format(i+1, scores[i]), end='\n\n')
            print(text, end='\n\n')


def generate_sample(data, tokenizer, model, num=1, eval_step=False, length=100, temperature=1, top_k=10, top_p=0.5, device=torch.device('cuda')):
    """ Generate summaries for "num" number of articles.
        Args:
            data = GPT21024Dataset object
            tokenizer = gpt/gpt2 tokenizer
            model = gpt/gpt2 model
            num = number of articles for which summaries has to be generated
            eval_step = can be True/False, checks generating during evaluation or not
    """
    for i in range(num):
        sample = data[i]
        idx = sample['sum_idx']
        context = sample['article'][:idx].tolist()
        summary = sample['article'][idx+1:][:100].tolist()
        generated_text = sample_seq(model, context, length, device, temperature, top_k, top_p)
        generated_text = generated_text[0, len(context):].tolist()
        text = tokenizer.convert_ids_to_tokens(generated_text,skip_special_tokens=True)
        text = tokenizer.convert_tokens_to_string(text)
        if eval_step==False:
            print('new_article', end='\n\n')
            print(tokenizer.decode(context), end='\n\n')
            print("generated_summary", end='\n\n')
            print(text, end='\n\n')
            print('actual_summary', end='\n\n')
            print(tokenizer.decode(summary), end='\n\n')
        else:
            print(tokenizer.decode(context), end='\n\n')
            print("generated_summary", end='\n\n')

In [ ]:
import os
import json
import numpy as np
import torch
from torch.utils.data import Dataset


class GPT21024Dataset(Dataset):

    def __init__(self, root_dir, ids_file, mode='train',length=None):
        self.root_dir = root_dir
        self.tokenizer = add_special_tokens()

        # with open(ids_file,'r') as f:
            # if mode=='train':
            #     self.idxs = np.array(json.load(f)['train_ids'])
            # elif mode=='valid':
            #     self.idxs = np.array(json.load(f)['valid_ids'])
            # elif mode=='test':
            #     self.idxs = np.array(json.load(f)['test_ids'])

            # self.idxs = self.idxs -min(self.idxs)

        self.idxs = os.listdir(root_dir)
        self.mode = mode
        if len == None:
            self.len = len(self.idxs)
        else:
            self.len = length

    def __len__(self):
        return self.len

    def __getitem__(self,idx):

        if self.mode=='valid':
            idx = self.idxs[-idx]
        elif self.mode=='test':
            idx = self.idxs[-idx-self.len]   # assuming valid and test set of same sizes
        else:
            idx = self.idxs[idx]
        # file_name = os.path.join(self.root_dir,str(idx)+".json")
        file_name = os.path.join(self.root_dir,str(idx))
        with open(file_name,'r') as f:
              data = json.load(f)
        text = self.tokenizer.encode(self.tokenizer.pad_token)*1024
        content = data['article'] + self.tokenizer.encode(self.tokenizer.sep_token) + data['abstract']
        text[:len(content)] = content
        text = torch.tensor(text)
        sample = {'article': text, 'sum_idx': len(data['article'])}
        return sample

In [ ]:
import argparse
from datetime import datetime
import os
import time

import numpy as np
from torch.optim import AdamW
from transformers import get_linear_schedule_with_warmup
from transformers import GPT2LMHeadModel
from torch.utils.tensorboard import SummaryWriter
import torch
from torch.nn import CrossEntropyLoss
import torch.nn.functional as F
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler
from tqdm import tnrange, tqdm_notebook




In [ ]:
# 确保设备为GPU或CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [18]:
# 参数解析器
parser = argparse.ArgumentParser()

# 默认超参数配置
parser.add_argument("--lr", default=5e-5, type=float, help="learning rate")
parser.add_argument("--seed", default=42, type=int, help="seed to replicate results")
parser.add_argument("--n_gpu", default=torch.cuda.device_count(), type=int, help="number of GPUs available")
parser.add_argument("--gradient_accumulation_steps", default=2, type=int, help="gradient accumulation steps")
parser.add_argument("--batch_size", default=1, type=int, help="batch size")
parser.add_argument("--num_workers", default=4, type=int, help="number of CPUs available")
parser.add_argument("--device", default=device, help="torch.device object")
parser.add_argument("--num_train_epochs", default=1, type=int, help="number of training epochs")
parser.add_argument("--output_dir", default='./output', type=str, help="path to save evaluation results")
parser.add_argument("--model_dir", default='./weights', type=str, help="path to save trained model")
parser.add_argument("--max_grad_norm", default=1.0, type=float, help="max gradient norm")
parser.add_argument("--root_dir", default='./CNN1/gpt2_1024_data', type=str, help="location of json dataset")
parser.add_argument("--ids_file", default='./CNN1/ids.json', type=str, help="location of train, valid, and test file indexes")

# 解析命令行参数
args = parser.parse_args([])

# 打印配置参数
print(f"Training configuration: {args}")


Training configuration: Namespace(lr=5e-05, seed=42, n_gpu=1, gradient_accumulation_steps=2, batch_size=1, num_workers=4, device=device(type='cuda'), num_train_epochs=1, output_dir='./output', model_dir='./weights', max_grad_norm=1.0, root_dir='./CNN1/gpt2_1024_data', ids_file='./CNN1/ids.json')


In [23]:
def train(args, model, tokenizer, train_dataset, valid_dataset, ignore_index):
    """ Trains GPT2 model and logs necessary details.
        Args:
            args: dict that contains all the necessary information passed by user while training
            model: finetuned gpt/gpt2 model
            tokenizer: GPT/GPT2 tokenizer
            train_dataset: GPT21024Dataset object for training data
            ignore_index: token not considered in loss calculation
    """
    writer = SummaryWriter('./output/logs')
    train_sampler = RandomSampler(train_dataset)
    train_dl = DataLoader(train_dataset, sampler=train_sampler, batch_size=args.batch_size, num_workers=args.num_workers)
    loss_fct = CrossEntropyLoss(ignore_index=ignore_index)  # Ignores padding token for loss calculation

    optimizer = AdamW(model.parameters(), lr=args.lr)

    total_steps = len(train_dl) * args.num_train_epochs

    scheduler = get_linear_schedule_with_warmup(
        optimizer,
        num_warmup_steps=100,
        num_training_steps=total_steps
    )

    global_step = 0
    tr_loss, logging_loss = 0.0, 0.0
    model.zero_grad()
    train_iterator = tnrange(int(args.num_train_epochs), desc="Epoch")

    set_seed(args)

    for _ in train_iterator:
        epoch_iterator = tqdm_notebook(train_dl, desc="Training")
        for step, batch in enumerate(epoch_iterator):
            inputs, labels = batch['article'].to(args.device), batch['article'].to(args.device)
            model.train()

            logits = model(inputs)[0]

            shift_logits = logits[..., batch['sum_idx']:-1, :].contiguous()
            shift_labels = labels[..., batch['sum_idx']+1:].contiguous()

            loss = loss_fct(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1))
            loss = loss / args.gradient_accumulation_steps
            loss.backward()

            torch.nn.utils.clip_grad_norm_(model.parameters(), args.max_grad_norm)
            tr_loss += loss.item()

            if (step + 1) % args.gradient_accumulation_steps == 0:
                optimizer.step()
                scheduler.step()
                model.zero_grad()
                global_step += 1

                writer.add_scalar('lr', scheduler.get_last_lr()[0], global_step)
                writer.add_scalar('loss', (tr_loss - logging_loss) / args.gradient_accumulation_steps, global_step)
                logging_loss = tr_loss
                print("loss:", loss.item(), end='\n\n')

                if (step + 1) / args.gradient_accumulation_steps == 1.0:
                    print('After 1st update: ', end='\n\n')
                    generate_sample(valid_dataset, tokenizer, model, num=2, eval_step=False, device=args.device)

            if (step + 1) % (10 * args.gradient_accumulation_steps) == 0:
                results = evaluate(args, model, valid_dataset, ignore_index, global_step)
                for key, value in results.items():
                    writer.add_scalar(f'eval_{key}', value, global_step)

                print(f'After {global_step + 1} updates: ', end='\n\n')
                generate_sample(valid_dataset, tokenizer, model, num=2, eval_step=True, device=args.device)

    writer.close()
    print("Training completed!")


In [20]:
def evaluate(args, model, eval_dataset, ignore_index, global_step=None):
    """ Returns perplexity score on validation dataset.
        Args:
            args: dict that contains all the necessary information passed by user while training
            model: finetuned gpt/gpt2 model
            eval_dataset: GPT21024Dataset object for validation data
            global_step: no. of times gradients have backpropagated
            ignore_index: token not considered in loss calculation
    """
    if not os.path.exists(args.output_dir):
        os.mkdir(args.output_dir)
    eval_output_dir = args.output_dir

    results = {}
    eval_sampler = SequentialSampler(eval_dataset)
    eval_dataloader = DataLoader(eval_dataset, sampler=eval_sampler, batch_size=args.batch_size)
    loss_fct = CrossEntropyLoss(ignore_index=ignore_index) #ignores padding token for loss calculation

    eval_loss = 0.0
    nb_eval_steps = 0
    model.eval()

    for batch in tqdm_notebook(eval_dataloader, desc="Evaluating"):
        inputs, labels = batch['article'].to(args.device), batch['article'].to(args.device)

        with torch.no_grad():
            logits = model(inputs)[0]
            idx = batch['sum_idx'].item() # index of separator token
            # only consider loss on reference summary just like seq2seq models
            shift_logits = logits[..., batch['sum_idx']:-1, :].contiguous()
            shift_labels = labels[..., batch['sum_idx']+1:].contiguous()
            lm_loss = loss_fct(shift_logits.view(-1, shift_logits.size(-1)), shift_labels.view(-1))
            eval_loss += lm_loss.mean().item()
        nb_eval_steps += 1

    eval_loss = eval_loss / nb_eval_steps
    perplexity = torch.exp(torch.tensor(eval_loss))

    result = {
        "perplexity": perplexity
    }
    print("perplexity:", perplexity.item())

    if global_step:
        output_eval_file = os.path.join(eval_output_dir, "eval_results.txt")
        with open(output_eval_file, "a") as f:
            for key in sorted(result.keys()):
                f.write('\n\n')
                f.write("time = %s, %s = %s, step = %s\n" % (datetime.now().strftime("%d/%m/%Y %H:%M:%S"), key, str(result[key]), str(global_step)))
    return result


In [ ]:
!unzip /content/CNN1/gpt2_1024_data.zip -d /content/CNN1


Archive:  /content/CNN1/gpt2_1024_data.zip
   creating: /content/CNN1/gpt2_1024_data/
  inflating: /content/CNN1/gpt2_1024_data/0.json  
  inflating: /content/CNN1/gpt2_1024_data/1.json  
  inflating: /content/CNN1/gpt2_1024_data/10.json  
  inflating: /content/CNN1/gpt2_1024_data/100.json  
  inflating: /content/CNN1/gpt2_1024_data/1000.json  
  inflating: /content/CNN1/gpt2_1024_data/1001.json  
  inflating: /content/CNN1/gpt2_1024_data/1002.json  
  inflating: /content/CNN1/gpt2_1024_data/1003.json  
  inflating: /content/CNN1/gpt2_1024_data/1004.json  
  inflating: /content/CNN1/gpt2_1024_data/1005.json  
  inflating: /content/CNN1/gpt2_1024_data/1006.json  
  inflating: /content/CNN1/gpt2_1024_data/1007.json  
  inflating: /content/CNN1/gpt2_1024_data/1008.json  
  inflating: /content/CNN1/gpt2_1024_data/1009.json  
  inflating: /content/CNN1/gpt2_1024_data/101.json  
  inflating: /content/CNN1/gpt2_1024_data/1010.json  
  inflating: /content/CNN1/gpt2_1024_data/1011.json  
  infl

In [21]:
# creating training and validation dataset object

train_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='train',length=3000) #training on only 3000 datasets
valid_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='valid',length=500)  #validation on only 500 datasets

In [ ]:
# load pretrained GPT2
tokenizer = add_special_tokens()
ignore_idx = tokenizer.pad_token_id
model = GPT2LMHeadModel.from_pretrained('gpt2')
model.resize_token_embeddings(len(tokenizer))
model.to(args.device)


Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

The new embeddings will be initialized from a multivariate normal distribution that has old embeddings' mean and covariance. As described in this article: https://nlp.stanford.edu/~johnhew/vocab-expansion.html. To disable this, use `mean_resizing=False`


GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50259, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50259, bias=False)
)

In [24]:
#training the model

start = time.time()
train(args, model, tokenizer, train_data, valid_data, ignore_idx)
print('total time: ', (time.time()-start)/60, " minutes", end='\n\n')

print('Saving trained model...')
model_file = os.path.join(args.model_dir, 'model_data{}_trained_after_{}_epochs_only_sum_loss_ignr_pad.bin'.format(len(train_data),args.num_train_epochs))
config_file = os.path.join(args.model_dir, 'config_data{}_trained_after_{}_epochs_only_sum_loss_ignr_pad.json'.format(len(train_data),args.num_train_epochs))
torch.save(model.state_dict(), model_file)
model.config.to_json_file(config_file)

<ipython-input-23-7fedab7acbbc>:28: TqdmDeprecationWarning: Please use `tqdm.notebook.trange` instead of `tqdm.tnrange`
  train_iterator = tnrange(int(args.num_train_epochs), desc="Epoch")


Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

<ipython-input-23-7fedab7acbbc>:33: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  epoch_iterator = tqdm_notebook(train_dl, desc="Training")


Training:   0%|          | 0/3000 [00:00<?, ?it/s]

loss: 1.5138691663742065

After 1st update: 



...

  0%|          | 0/100 [00:00<?, ?it/s]

-LRB- EW.com -RRB- -- `` Facts of Life '' star and `` Survivor '' schemer Lisa Whelchel has West Nile virus . The 49-year-old actress tweeted her condition , writing , `` Dr. just called with blood test results ... I have West Nile . Ugh . I 'm fine , just tired . Takes a year to recover . '' It 's unknown where she contracted the illness , which can be spread by mosquitoes . 10 Most Successful Mouseketeers . `` Survivor : Philippines '' wrapped its production in April . Approximately 5,000 Americans have been infected by the illness this year , and Texas , where Whelchel lives , is one of the hardest-hit states . Whelchel later tweeted , `` I 've been very touched by all the sweet tweets . Other than tired , I 'm feeling fine & expecting a full recovery . So grateful for you . Thanks !? '' See the original article at EW.com . CLICK HERE to Try 2 RISK FREE issues of Entertainment Weekly . © 2011 Entertainment Weekly and Time Inc. . All rights reserved .

generated_summary



  0%|          | 0/100 [00:00<?, ?it/s]

-LRB- CNN -RRB- -- A U.S. District Court judge has overturned South Carolina 's ban on same-sex marriage . The ruling , by Judge Richard M. Gergel in Charleston , does not mean an immediate issuance of marriage licenses for same-sex couples , however . The judge set the order to go into effect on November 20 , to give opponents time to appeal if they wish . Gergel , who was appointed by President Barack Obama , issued a permanent injunction against enforcement of provisions of the state constitution or state laws or policy `` to the extent that they seek to prohibit the marriage of same sex couples . '' If the judge 's ruling stands and same-sex marriage becomes legal , South Carolina would become the 33rd state in which same-sex marriage has become legal . Same-sex marriage is under court review in Arkansas , Florida , Kansas , Louisiana and Texas . It is banned in 12 other states .

generated_summary

Training completed!
total time:  136.33032074769338  minutes

Saving trained model.

RuntimeError: Parent directory ./weights does not exist.

In [25]:
print(model)


GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50259, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50259, bias=False)
)


In [26]:
import os

# 设置保存路径
args.model_dir = "/content/weights"

# 确保目录存在
os.makedirs(args.model_dir, exist_ok=True)

# 构造文件名
model_file = os.path.join(
    args.model_dir,
    'model_data{}_trained_after_{}_epochs_only_sum_loss_ignr_pad.bin'.format(len(train_data), args.num_train_epochs)
)
config_file = os.path.join(
    args.model_dir,
    'config_data{}_trained_after_{}_epochs_only_sum_loss_ignr_pad.json'.format(len(train_data), args.num_train_epochs)
)

# 保存模型参数和配置
torch.save(model.state_dict(), model_file)
model.config.to_json_file(config_file)

print("✅ 模型和配置文件已保存到 /content/weights")


✅ 模型和配置文件已保存到 /content/weights


接下来开始验证模型


In [27]:
# using the same validation and training data as during training
tokenizer = add_special_tokens()
# train_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='train',length=3000)
# valid_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='valid',length=500)
test_data = GPT21024Dataset(args.root_dir,args.ids_file,mode='test',length=500)

In [28]:
from transformers import GPT2Config
model_file = "/content/weights/model_data3000_trained_after_1_epochs_only_sum_loss_ignr_pad.bin"
config_file = "/content/weights/config_data3000_trained_after_1_epochs_only_sum_loss_ignr_pad.json"

config = GPT2Config.from_json_file(config_file)
model = GPT2LMHeadModel(config)
state_dict = torch.load(model_file)
model.load_state_dict(state_dict)
model.eval()
model.to(args.device)

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50259, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50259, bias=False)
)

In [30]:
generate_sample(
    test_data,
    tokenizer,
    model,
    num=2,
    length=100,
    temperature=0.8,  # 更低温度 → 更稳定
    top_k=50,         # 提高多样性
    top_p=0.95,       # nucleus sampling 控制
    device=args.device
)


<ipython-input-5-cd85466fe1e8>:71: TqdmDeprecationWarning: Please use `tqdm.notebook.trange` instead of `tqdm.tnrange`
  for _ in tnrange(length):


  0%|          | 0/100 [00:00<?, ?it/s]

new_article

Washington -LRB- CNN -RRB- -- The Washington Monument was closed indefinitely as engineers study damage and ways to repair cracks at the top of the capital 's iconic structure caused by the 5.8-magnitude earthquake that rattled the East Coast this week . Tuesday 's quake caused a 4-foot crack in the pyramidion at the top of the 555-foot obelisk and several pieces of mortar fell inside the monument 's observation area during the earthquake , a National Park Service spokesman said . An outside structural engineering firm is conducting a thorough damage assessment , and the monument may not be reopened to the public until after any necessary repairs are completed , the spokesman added . `` It could be awhile and the most important thing is the visitors ' safety is key , is paramount , is chief and we 're not going to risk anyone going in and becoming injured , '' National Park Service spokesman Bill Line said . The Washington National Cathedral also was closed after sustainin

  0%|          | 0/100 [00:00<?, ?it/s]

new_article

-LRB- CNN -RRB- -- Investigators involved in the case of serial killing suspect Elias Abuelazam went to Louisville , Kentucky , on Monday to retrieve two of his bags , Michigan police said . Abuelazam is suspected of slashing 18 victims in Michigan , Virginia and Ohio , killing five . He was arrested at Hartsfield Jackson International Airport in Atlanta , Georgia , last week as he was attempting to board a flight to Israel . Abuelazam has agreed to be sent back to Michigan to face charges , but he remains in custody in Atlanta . Michigan authorities have some two weeks to pick him up . As of Monday afternoon , police said they do not know how , or when , Abuelazam will be transported . He traveled last week from Detroit , Michigan , to Louisville , before heading to Atlanta , police said . The airline company misplaced his luggage and the bags never made it to Atlanta , they added . Michigan authorities said they took the two bags back with them . Lt. Steven Sipes of the 

In [35]:
from bs4 import BeautifulSoup
from googlesearch import search
import numpy as np
import requests
def sentences_from_query(query):
    if query.startswith("http"):
        url = query
    else:
        # 获取第一个搜索结果
        url = list(search(query))[0]
    print(url)

    page = requests.get(url).text
    soup = BeautifulSoup(page, 'html.parser')
    p_tags = soup.find_all('p')
    p_tags_text = " ".join([tag.get_text().strip() for tag in p_tags])
    return p_tags_text

In [36]:
article = sentences_from_query("neural embedding")
article = tokenizer.encode(article)[:900]


https://medium.com/towards-data-science/neural-network-embeddings-explained-4d028e6f0526


Token indices sequence length is longer than the specified maximum sequence length for this model (2018 > 1024). Running this sequence through the model will result in indexing errors


In [37]:
# 使用模型生成指定长度的文本
generated_text = sample_seq(model, article, 50, args.device, temperature=1, top_k=10, top_p=0.5)

# 从生成的文本中仅取生成的部分（即不包括原始的输入部分）
# 这里假设 generated_text 是一个形状为 [1, len(article) + 50] 的张量
generated_text = generated_text[0, len(article):].tolist()

# 将生成的 token IDs 转换为对应的单词或子词，跳过特殊 token（如 [CLS], [SEP], [PAD]）
text = tokenizer.convert_ids_to_tokens(generated_text, skip_special_tokens=True)

# 将转换后的 token 列表拼接成一个完整的字符串
# 这里的 text 是最终生成的文本
text = tokenizer.convert_tokens_to_string(text)




<ipython-input-5-cd85466fe1e8>:71: TqdmDeprecationWarning: Please use `tqdm.notebook.trange` instead of `tqdm.tnrange`
  for _ in tnrange(length):


  0%|          | 0/50 [00:00<?, ?it/s]

In [38]:
print("Article: \n")
print(tokenizer.decode(article))
print("------------------------------------------------------------ \n")
print("Generated Summary: \n")
print(text)

Article: 

Sign up Sign in Sign up Sign in  An archive of data science, data analytics, data engineering, machine learning, and artificial intelligence writing from the former Towards Data Science Medium publication.  -- 25 Listen Share Applications of neural networks have expanded significantly in recent years from image segmentation to natural language processing to time-series forecasting. One notably successful use of deep learning is embedding, a method used to represent discrete variables as continuous vectors. This technique has found practical applications with word embeddings for machine translation and entity embeddings for categorical variables. In this article, I’ll explain what neural network embeddings are, why we want to use them, and how they are learned. We’ll go through these concepts in the context of a real problem I’m working on: representing all the books on Wikipedia as vectors to create a book recommendation system. An embedding is a mapping of a discrete — cate

In [39]:
!pip install transformers huggingface_hub


In [40]:
from huggingface_hub import login

login()


In [41]:
from huggingface_hub import create_repo

create_repo("gpt2-summerization", private=True)  # private=True 设置为私有仓库，默认为公开


RepoUrl('https://huggingface.co/felix000ooo/gpt2-summerization', endpoint='https://huggingface.co', repo_type='model', repo_id='felix000ooo/gpt2-summerization')

In [42]:
from huggingface_hub import upload_file

# 设置模型库的路径
repo_id = "felix000ooo/gpt2-summerization"

# 上传模型文件和配置文件
upload_file(
    path_or_fileobj="/content/weights/model_data3000_trained_after_1_epochs_only_sum_loss_ignr_pad.bin",
    path_in_repo="model.bin",  # 在仓库中保存的文件名
    repo_id=repo_id
)

upload_file(
    path_or_fileobj="/content/weights/config_data3000_trained_after_1_epochs_only_sum_loss_ignr_pad.json",
    path_in_repo="config.json",  # 在仓库中保存的文件名
    repo_id=repo_id
)


model_data3000_trained_after_1_epochs_only_sum_loss_ignr_pad.bin:   0%|          | 0.00/498M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/felix000ooo/gpt2-summerization/commit/dbde145361e4b4c53b037c159cbc7c85d7dcdc3b', commit_message='Upload config.json with huggingface_hub', commit_description='', oid='dbde145361e4b4c53b037c159cbc7c85d7dcdc3b', pr_url=None, repo_url=RepoUrl('https://huggingface.co/felix000ooo/gpt2-summerization', endpoint='https://huggingface.co', repo_type='model', repo_id='felix000ooo/gpt2-summerization'), pr_revision=None, pr_num=None)